In [1]:
import json
import numpy as np
import pickle
import re
import string
import nltk
import pandas as pd
import spacy
import re
import string
from gensim import matutils, models
import scipy.sparse
from collections import Counter
from sklearn.feature_extraction import text 
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
spacy.prefer_gpu()
import logging  # Setting up the loggings to monitor gensim
logging.basicConfig(format="%(levelname)s - %(asctime)s: %(message)s", datefmt= '%H:%M:%S', level=logging.INFO)


In [2]:
from glob import glob
import re
import string
import funcy as fp
from gensim import models
from gensim.corpora import Dictionary, MmCorpus
import nltk
import pandas as pd

In [3]:
data_df = pd.read_pickle('cleaned_list_df.pickle')
data_df = data_df.T
data_df

wsb  \
0       in the future when apple is at  a share your g...   
1       you ever stare at your account and think wow h...   
2                                  buy  at the top gang 🤡   
3       almost responded to an email with thanks retar...   
4       top trending tickers sentiments and options on...   
...                                                   ...   
101136                                               none   
101137                                               none   
101138                                               none   
101139                                               none   
101140                                               none   

                                                  science  \
0        the children were not motivated by achieving ...   
1       also proved children like to gamble according ...   
2       kind of like how gamers go through rpg games e...   
3       i teach elementary pe  to  year olds one of th...   
4       wouldnt this make lootmystery boxes even worse...   
...                                                   ...   
101136                                               none   
101137                                               none   
101138                                               none   
101139                                               none   
101140                                               none   

                                                      ama  \
0                      tldr do whatever the fuck you want   
1          so youre telling me people on the internet lie   
2                                                           
3       this is so funny this subreddit got fucked by ...   
4       a note about celebrity request bans when riama...   
...                                                   ...   
101136                                               none   
101137                                               none   
101138                                               none   
101139                                               none   
101140                                               none   

                                                askreddit  \
0       victorias secret was originally supposed to be...   
1       the ford mustang  it was supposed to be a car ...   
2                           heels if i remember correctly   
3       is this how family feud gets new questions and...   
4       skirts used to be worn in battle by men for mo...   
...                                                   ...   
101136                                              maybe   
101137  is it my cake day i have always wondered how p...   
101138  theres a cake emoji next to your username on y...   
101139  i think my problem is that im using narwhal ed...   
101140                                                lol   

                                                worldnews  \
0             so was there any posts left after the purge   
1       ok just for some context  facebook has an esti...   
2       they still havent taken down my post about mar...   
3       why does facebook have a fake news problem  be...   
4       a lot of karens are going to be be saying they...   
...                                                   ...   
101136                                               none   
101137                                               none   
101138                                               none   
101139                                               none   
101140                                               none   

                                                    funny  \
0                           but i wanted the robot ferret   
1       haha suck it you fools i already got my roboti...   
2         this not funny rule number oh i forget carry on   
3                     but the nigerian guy is legit right   
4       bruh when i was younger i went to a farm this ...   
...                    

In [4]:
wsb = data_df['wsb'].tolist()
science = data_df['science'].tolist()
ama = data_df['ama'].tolist()
askreddit = data_df['askreddit'].tolist()
worldnews = data_df['worldnews'].tolist()
funny = data_df['funny'].tolist()
dankmemes = data_df['dankmemes'].tolist()
memes = data_df['memes'].tolist()
nosleep = data_df['nosleep'].tolist()
psychology = data_df['psychology'].tolist()
politics = data_df['politics'].tolist()
cscareerquestions = data_df['cscareerquestions'].tolist()
writingprompts = data_df['writingprompts'].tolist()

full_list = wsb + science + ama + askreddit + worldnews + funny + dankmemes + memes + nosleep + psychology + politics + cscareerquestions + writingprompts
full_list

['in the future when apple is at  a share your gran kids will ask why you didnt buy apple at  and youll answer with i bought corn instead',
 'you ever stare at your account and think wow how did i put  into options and think that was safe',
 'buy  at the top gang 🤡',
 'almost responded to an email with thanks retard because  of my social interaction is now through this sub',
 'top trending tickers sentiments and options on rwallstreetbets for the day of august    ────────────────  trending tickers  tickercompanymentionsbulls  bearspricechangepe  tslatesla    spyexchange traded    slvexchange traded    aaplapple    cornexchange traded    rktrocket companies    msftmicrosoft    amdadvanced micro    bathe boeing    fbfacebook    prplpurple innovation    qqqexchange traded    netcloudflare    cscocisco systems    nvdanvidia      ────────────────  trending options  tickerstriketypeexpiration                   ────────────────  trending sentiment  sentimentcomments       ────────────────  ot

In [5]:
vectorizer = TfidfVectorizer(stop_words='english',
                             binary=True, ngram_range=(1,2))

doc_word = vectorizer.fit_transform(askreddit)
words = list(np.asarray(vectorizer.get_feature_names())) 
doc_word

<101141x752319 sparse matrix of type '<class 'numpy.float64'>'
	with 2111926 stored elements in Compressed Sparse Row format>

In [7]:
doc_word

<101141x752319 sparse matrix of type '<class 'numpy.float64'>'
	with 2111926 stored elements in Compressed Sparse Row format>

In [8]:
# cvn = TfidfVectorizer(ngram_range=(1,1))
# data_cvn = cvn.fit_transform(full_list)
# data_dtmn = pd.DataFrame(data_cvn.toarray(), columns=cvn.get_feature_names()).T
# # data_dtmn.columns = data_df.index
# data_dtmn

In [6]:
# Create the gensim corpus
corpusn = matutils.Sparse2Corpus(scipy.sparse.csr_matrix(doc_word))

# Create the vocabulary dictionary
id2wordn = dict((v, k) for k, v in vectorizer.vocabulary_.items())
word2id = dict((k, v) for k, v in vectorizer.vocabulary_.items())

In [7]:
# Let's start with 2 topics
ldan = models.LdaMulticore(corpus=corpusn, num_topics=20, id2word=id2wordn, passes=50)
ldan.print_topics()

INFO - 17:07:24: using symmetric alpha at 0.05
INFO - 17:07:24: using symmetric eta at 0.05
INFO - 17:07:24: using serial LDA version on this node
INFO - 17:07:25: running online LDA training, 20 topics, 50 passes over the supplied corpus of 752319 documents, updating every 30000 documents, evaluating every ~300000 documents, iterating 50x with a convergence threshold of 0.001000
INFO - 17:07:25: training LDA model using 15 processes
INFO - 17:07:25: PROGRESS: pass 0, dispatched chunk #0 = documents up to #2000/752319, outstanding queue size 1
INFO - 17:07:25: PROGRESS: pass 0, dispatched chunk #1 = documents up to #4000/752319, outstanding queue size 2
INFO - 17:07:25: PROGRESS: pass 0, dispatched chunk #2 = documents up to #6000/752319, outstanding queue size 3
INFO - 17:07:25: PROGRESS: pass 0, dispatched chunk #3 = documents up to #8000/752319, outstanding queue size 4
INFO - 17:07:25: PROGRESS: pass 0, dispatched chunk #4 = documents up to #10000/752319, outstanding queue size 5
I

INFO - 17:07:41: PROGRESS: pass 0, dispatched chunk #42 = documents up to #86000/752319, outstanding queue size 7
INFO - 17:07:41: PROGRESS: pass 0, dispatched chunk #43 = documents up to #88000/752319, outstanding queue size 8
INFO - 17:07:41: PROGRESS: pass 0, dispatched chunk #44 = documents up to #90000/752319, outstanding queue size 9
INFO - 17:07:41: PROGRESS: pass 0, dispatched chunk #45 = documents up to #92000/752319, outstanding queue size 10
INFO - 17:07:41: PROGRESS: pass 0, dispatched chunk #46 = documents up to #94000/752319, outstanding queue size 11
INFO - 17:07:41: PROGRESS: pass 0, dispatched chunk #47 = documents up to #96000/752319, outstanding queue size 12
INFO - 17:07:41: PROGRESS: pass 0, dispatched chunk #48 = documents up to #98000/752319, outstanding queue size 13
INFO - 17:07:41: PROGRESS: pass 0, dispatched chunk #49 = documents up to #100000/752319, outstanding queue size 14
INFO - 17:07:41: PROGRESS: pass 0, dispatched chunk #50 = documents up to #102000/

INFO - 17:07:55: topic diff=0.010252, rho=0.137361
INFO - 17:07:55: PROGRESS: pass 0, dispatched chunk #88 = documents up to #178000/752319, outstanding queue size 22
INFO - 17:08:03: merging changes from 40000 documents into a model of 752319 documents
INFO - 17:08:03: topic #4 (0.050): 0.000*"bioindividuality medication" + 0.000*"ankle" + 0.000*"anime context" + 0.000*"alcoholic hide" + 0.000*"away head" + 0.000*"california like" + 0.000*"add fucked" + 0.000*"applications ability" + 0.000*"boyfriends mouth" + 0.000*"ann frank"
INFO - 17:08:03: topic #2 (0.050): 0.000*"advantage work" + 0.000*"ate small" + 0.000*"ate salt" + 0.000*"adjustable rate" + 0.000*"away tomorrow" + 0.000*"affinity" + 0.000*"cared figure" + 0.000*"celestia ruled" + 0.000*"chopping" + 0.000*"big analysis"
INFO - 17:08:03: topic #11 (0.050): 0.000*"backpack drawer" + 0.000*"authority feel" + 0.000*"bachelors" + 0.000*"ability incredibly" + 0.000*"blunt nice" + 0.000*"chinchester thanks" + 0.000*"bag things" + 0.

INFO - 17:08:15: PROGRESS: pass 0, dispatched chunk #133 = documents up to #268000/752319, outstanding queue size 20
INFO - 17:08:15: PROGRESS: pass 0, dispatched chunk #134 = documents up to #270000/752319, outstanding queue size 21
INFO - 17:08:15: PROGRESS: pass 0, dispatched chunk #135 = documents up to #272000/752319, outstanding queue size 22
INFO - 17:08:15: PROGRESS: pass 0, dispatched chunk #136 = documents up to #274000/752319, outstanding queue size 23
INFO - 17:08:15: PROGRESS: pass 0, dispatched chunk #137 = documents up to #276000/752319, outstanding queue size 24
INFO - 17:08:15: PROGRESS: pass 0, dispatched chunk #138 = documents up to #278000/752319, outstanding queue size 25
INFO - 17:08:16: PROGRESS: pass 0, dispatched chunk #139 = documents up to #280000/752319, outstanding queue size 26
INFO - 17:08:21: merging changes from 42000 documents into a model of 752319 documents
INFO - 17:08:21: topic #14 (0.050): 0.000*"chippewa indians" + 0.000*"actually regret" + 0.000

INFO - 17:08:34: PROGRESS: pass 0, dispatched chunk #178 = documents up to #358000/752319, outstanding queue size 24
INFO - 17:08:34: PROGRESS: pass 0, dispatched chunk #179 = documents up to #360000/752319, outstanding queue size 25
INFO - 17:08:34: PROGRESS: pass 0, dispatched chunk #180 = documents up to #362000/752319, outstanding queue size 26
INFO - 17:08:34: PROGRESS: pass 0, dispatched chunk #181 = documents up to #364000/752319, outstanding queue size 27
INFO - 17:08:34: PROGRESS: pass 0, dispatched chunk #182 = documents up to #366000/752319, outstanding queue size 28
INFO - 17:08:34: PROGRESS: pass 0, dispatched chunk #183 = documents up to #368000/752319, outstanding queue size 29
INFO - 17:08:34: PROGRESS: pass 0, dispatched chunk #184 = documents up to #370000/752319, outstanding queue size 30
INFO - 17:08:34: PROGRESS: pass 0, dispatched chunk #185 = documents up to #372000/752319, outstanding queue size 31
INFO - 17:08:34: PROGRESS: pass 0, dispatched chunk #186 = docum

...

INFO - 19:28:19: topic #18 (0.050): 0.002*"carwash dodgeball" + 0.000*"chains eapol" + 0.000*"chains equality" + 0.000*"careful says" + 0.000*"buying home" + 0.000*"aint making" + 0.000*"avocados pay" + 0.000*"came hands" + 0.000*"breathe convinient" + 0.000*"chest face"
INFO - 19:28:19: topic diff=0.001093, rho=0.048441
INFO - 19:28:19: PROGRESS: pass 49, dispatched chunk #281 = documents up to #564000/752319, outstanding queue size 4
INFO - 19:28:19: PROGRESS: pass 49, dispatched chunk #282 = documents up to #566000/752319, outstanding queue size 2
INFO - 19:28:20: PROGRESS: pass 49, dispatched chunk #283 = documents up to #568000/752319, outstanding queue size 3
INFO - 19:28:20: PROGRESS: pass 49, dispatched chunk #284 = documents up to #570000/752319, outstanding queue size 3
INFO - 19:28:20: PROGRESS: pass 49, dispatched chunk #285 = documents up to #572000/752319, outstanding queue size 4
INFO - 19:28:20: PROGRESS: pass 49, dispatched chunk #286 = documents up to #574000/752319, 

INFO - 19:28:36: PROGRESS: pass 49, dispatched chunk #323 = documents up to #648000/752319, outstanding queue size 5
INFO - 19:28:36: PROGRESS: pass 49, dispatched chunk #324 = documents up to #650000/752319, outstanding queue size 6
INFO - 19:28:36: PROGRESS: pass 49, dispatched chunk #325 = documents up to #652000/752319, outstanding queue size 7
INFO - 19:28:36: PROGRESS: pass 49, dispatched chunk #326 = documents up to #654000/752319, outstanding queue size 8
INFO - 19:28:36: PROGRESS: pass 49, dispatched chunk #327 = documents up to #656000/752319, outstanding queue size 9
INFO - 19:28:36: PROGRESS: pass 49, dispatched chunk #328 = documents up to #658000/752319, outstanding queue size 10
INFO - 19:28:38: PROGRESS: pass 49, dispatched chunk #329 = documents up to #660000/752319, outstanding queue size 6
INFO - 19:28:38: PROGRESS: pass 49, dispatched chunk #330 = documents up to #662000/752319, outstanding queue size 7
INFO - 19:28:38: PROGRESS: pass 49, dispatched chunk #331 = doc

INFO - 19:28:51: PROGRESS: pass 49, dispatched chunk #368 = documents up to #738000/752319, outstanding queue size 16
INFO - 19:28:51: PROGRESS: pass 49, dispatched chunk #369 = documents up to #740000/752319, outstanding queue size 17
INFO - 19:28:51: PROGRESS: pass 49, dispatched chunk #370 = documents up to #742000/752319, outstanding queue size 18
INFO - 19:28:51: PROGRESS: pass 49, dispatched chunk #371 = documents up to #744000/752319, outstanding queue size 19
INFO - 19:28:52: PROGRESS: pass 49, dispatched chunk #372 = documents up to #746000/752319, outstanding queue size 19
INFO - 19:28:52: PROGRESS: pass 49, dispatched chunk #373 = documents up to #748000/752319, outstanding queue size 20
INFO - 19:28:52: PROGRESS: pass 49, dispatched chunk #374 = documents up to #750000/752319, outstanding queue size 21
INFO - 19:28:52: PROGRESS: pass 49, dispatched chunk #375 = documents up to #752000/752319, outstanding queue size 22
INFO - 19:28:52: PROGRESS: pass 49, dispatched chunk #37

INFO - 19:29:04: topic #15 (0.050): 0.000*"cartel executions" + 0.000*"better finger" + 0.000*"change tldr" + 0.000*"antipoor sentiment" + 0.000*"change basically" + 0.000*"best forethought" + 0.000*"bathroom year" + 0.000*"away hangs" + 0.000*"beneficial learning" + 0.000*"banging whilst"
INFO - 19:29:04: topic #16 (0.050): 0.000*"britannia unpredictable" + 0.000*"aboard lets" + 0.000*"boompa" + 0.000*"cements" + 0.000*"ah dont" + 0.000*"boyfriend card" + 0.000*"actively say" + 0.000*"aang feel" + 0.000*"achievements think" + 0.000*"bra looks"
INFO - 19:29:04: topic #17 (0.050): 0.001*"cardboard going" + 0.001*"business does" + 0.000*"able rock" + 0.000*"abortion anti" + 0.000*"aang atlab" + 0.000*"able multiple" + 0.000*"changed lives" + 0.000*"absence facebook" + 0.000*"able respond" + 0.000*"chances wont"
INFO - 19:29:04: topic #18 (0.050): 0.001*"carwash dodgeball" + 0.000*"chains equality" + 0.000*"chains eapol" + 0.000*"butterfly clips" + 0.000*"amazing looking" + 0.000*"army fa

[(0,
  '0.001*"breakup ex" + 0.001*"america gives" + 0.001*"bread vp" + 0.001*"cause evidence" + 0.000*"aisle" + 0.000*"ahhh good" + 0.000*"attenborough knows" + 0.000*"challenging im" + 0.000*"atlantathe" + 0.000*"check forget"'),
 (1,
  '0.001*"cartwright" + 0.001*"chips thats" + 0.001*"caught pictures" + 0.000*"children baby" + 0.000*"agencies order" + 0.000*"agree helpful" + 0.000*"believe fucks" + 0.000*"better meds" + 0.000*"beers taste" + 0.000*"began dancing"'),
 (2,
  '0.000*"account says" + 0.000*"account said" + 0.000*"bernie like" + 0.000*"blowing kinda" + 0.000*"boat nah" + 0.000*"caesar including" + 0.000*"braces illuminating" + 0.000*"bothered charged" + 0.000*"cases ended" + 0.000*"bernie make"'),
 (3,
  '0.001*"change station" + 0.001*"caught people" + 0.001*"business friend" + 0.001*"carved circus" + 0.001*"cause aint" + 0.001*"cains" + 0.001*"car life" + 0.000*"bob fucking" + 0.000*"bad lived" + 0.000*"bicycle bike"'),
 (4,
  '0.000*"car locked" + 0.000*"changed larg

In [8]:
ldan.save('askreddit_bigrams.model')

INFO - 19:29:04: saving LdaState object under askreddit_bigrams.model.state, separately None
INFO - 19:29:04: storing np array 'sstats' to askreddit_bigrams.model.state.sstats.npy
INFO - 19:29:04: saved askreddit_bigrams.model.state
INFO - 19:29:04: saving LdaMulticore object under askreddit_bigrams.model, separately ['expElogbeta', 'sstats']
INFO - 19:29:04: storing np array 'expElogbeta' to askreddit_bigrams.model.expElogbeta.npy
INFO - 19:29:04: not storing attribute id2word
INFO - 19:29:04: not storing attribute dispatcher
INFO - 19:29:04: not storing attribute state
INFO - 19:29:04: saved askreddit_bigrams.model


In [9]:
import pyLDAvis.gensim as gensimvis
import pyLDAvis

In [10]:
from gensim import corpora
d = corpora.Dictionary()
d.id2token = id2wordn
d.token2id = word2id

## 20 topics, tdfidf, askreddit

In [11]:
vis_data = gensimvis.prepare(ldan, corpusn, d)
pyLDAvis.display(vis_data)

INFO - 19:44:28: Note: NumExpr detected 16 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO - 19:44:28: NumExpr defaulting to 8 threads.


## 10 topics, TF-IDF'ed

In [27]:
vis_data = gensimvis.prepare(ldan, corpusn, d)
pyLDAvis.display(vis_data)

## 10 topics, CountVectorized

In [20]:
vis_data = gensimvis.prepare(ldan, corpusn, d)
pyLDAvis.display(vis_data)

INFO - 14:13:40: Note: NumExpr detected 16 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO - 14:13:40: NumExpr defaulting to 8 threads.
